In [1]:
import pandas as pd
import numpy as np
import tensorflow as tf
import datetime as DT
from tensorflow import keras
from sklearn.model_selection import train_test_split
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Activation,Dense, BatchNormalization,Dropout
from tensorflow.keras import optimizers
import os
from matplotlib import pyplot as plt
from sklearn import svm, datasets
from sklearn.datasets import make_regression
from sklearn.multioutput import MultiOutputRegressor
from sklearn.svm import SVR
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_squared_error, mean_absolute_error
from sklearn.pipeline import Pipeline
from sklearn.multioutput import MultiOutputClassifier
from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import GridSearchCV
from sklearn.multioutput import MultiOutputRegressor
from sklearn.model_selection import GridSearchCV
from sklearn.pipeline import Pipeline

In [2]:
patients = pd.read_csv('./maindata/patients.csv')
allergies = pd.read_csv('./maindata/allergies.csv')

In [3]:
allergies = allergies[allergies.CATEGORY != 'medication']
print(len(allergies['CODE'].unique()))

15


In [4]:
AllergiesDetails = allergies[['CODE','DESCRIPTION','CATEGORY','REACTION1','DESCRIPTION1','SEVERITY1','REACTION2','DESCRIPTION2','SEVERITY2']]
AllergiesDetails = AllergiesDetails.drop_duplicates(subset='CODE',keep='last')

In [5]:
AllergiesDetails.to_csv('AllergiesList.csv',index=False)

In [6]:
allergies = allergies[['PATIENT','CODE','START']]

In [7]:
allergies = pd.merge(allergies,patients,how='left',left_on='PATIENT',right_on='Id')

In [8]:
allergies=allergies[['START','BIRTHDATE','LAT','LON','CODE']]
allergies['START'] = pd.to_datetime(allergies['START'], errors='coerce')
allergies['BIRTHDATE'] = pd.to_datetime(allergies['BIRTHDATE'], errors='coerce')

In [9]:
allergies['AGE']=allergies['BIRTHDATE']
allergies['AGE']=pd.to_numeric(allergies['AGE'].values)/10**9

In [10]:
allergies=allergies[['AGE','LAT','LON','CODE']]

In [11]:
allergies.to_csv('CleanedData.csv')

In [12]:
allergies.head()

AGE        LAT        LON       CODE
0  1.507334e+09  41.930492 -71.003337  288328004
1  1.507334e+09  41.930492 -71.003337   84489001
2  1.507334e+09  41.930492 -71.003337  260147004
3  1.507334e+09  41.930492 -71.003337  264287008
4  1.507334e+09  41.930492 -71.003337  782576004

In [13]:
allergies_label = allergies.pop('CODE')

In [14]:
allergies_labels = pd.get_dummies(allergies_label,prefix="allergy")

In [15]:
allergies = pd.concat([allergies,allergies_labels],axis=1)

## Splitting Data in training and test

In [16]:
complete_train_dataset, complete_test_dataset = train_test_split(allergies,test_size=0.1)
# complete_test_dataset,complete_valid_dataset = train_test_split(temp_test_dataset,test_size=0.5)

In [17]:
train_dataset = complete_train_dataset.iloc[:,0:3]
train_labels = complete_train_dataset.iloc[:,3:]

In [18]:
test_dataset = complete_test_dataset.iloc[:,0:3]
test_labels = complete_test_dataset.iloc[:,3:]

#### Normalizing data

In [19]:
train_stats = train_dataset.describe()
train_stats = train_stats.transpose()


In [20]:
def norm(x):
    return (x-train_stats['mean'])/train_stats['std']

normed_train_data = norm(train_dataset)
normed_test_data = norm(test_dataset)


In [21]:
print(normed_test_data.shape[1])
print(train_labels.shape[1])

3
15


In [22]:

# model = Pipeline(steps=[('svr',SVR()),('lr_multi',MultiOutputClassifier(LogisticRegression()))])
# # model = MultiOutputRegressor(svr)
# model = model.fit(train_dataset,train_labels)
                        
# Create the SVR regressor
# svr = SVR(epsilon=0.2)

# Create the Multioutput Regressor
# model = MultiOutputRegressor(svr)

model = Pipeline([('reg', MultiOutputRegressor(SVR()))])


grid_param_svr = {
    'reg__estimator__C': [0.01,0.1,1],
    'reg__estimator__epsilon':[0.1,0.2],
    'reg__estimator__degree':[2,3]
}

gs_svr = (GridSearchCV( estimator=model, 
                        param_grid=grid_param_svr, 
                        cv=20,
                        scoring = 'accuracy',
                        n_jobs = -1,
                        refit=True)
         )

gs_svr = gs_svr.fit(train_dataset,train_labels)


/Users/vidhi/Downloads/yes/envs/tf_m1/lib/python3.8/site-packages/sklearn/model_selection/_validation.py:776: UserWarning: Scoring failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "/Users/vidhi/Downloads/yes/envs/tf_m1/lib/python3.8/site-packages/sklearn/model_selection/_validation.py", line 767, in _score
    scores = scorer(estimator, X_test, y_test)
  File "/Users/vidhi/Downloads/yes/envs/tf_m1/lib/python3.8/site-packages/sklearn/metrics/_scorer.py", line 219, in __call__
    return self._score(
  File "/Users/vidhi/Downloads/yes/envs/tf_m1/lib/python3.8/site-packages/sklearn/metrics/_scorer.py", line 267, in _score
    return self._sign * self._score_func(y_true, y_pred, **self._kwargs)
  File "/Users/vidhi/Downloads/yes/envs/tf_m1/lib/python3.8/site-packages/sklearn/metrics/_classification.py", line 211, in accuracy_score
    y_type, y_true, y_pred = _check_targets(y_true, y_pred)
  File "/U

/Users/vidhi/Downloads/yes/envs/tf_m1/lib/python3.8/site-packages/sklearn/model_selection/_validation.py:776: UserWarning: Scoring failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "/Users/vidhi/Downloads/yes/envs/tf_m1/lib/python3.8/site-packages/sklearn/model_selection/_validation.py", line 767, in _score
    scores = scorer(estimator, X_test, y_test)
  File "/Users/vidhi/Downloads/yes/envs/tf_m1/lib/python3.8/site-packages/sklearn/metrics/_scorer.py", line 219, in __call__
    return self._score(
  File "/Users/vidhi/Downloads/yes/envs/tf_m1/lib/python3.8/site-packages/sklearn/metrics/_scorer.py", line 267, in _score
    return self._sign * self._score_func(y_true, y_pred, **self._kwargs)
  File "/Users/vidhi/Downloads/yes/envs/tf_m1/lib/python3.8/site-packages/sklearn/metrics/_classification.py", line 211, in accuracy_score
    y_type, y_true, y_pred = _check_targets(y_true, y_pred)
  File "/U

/Users/vidhi/Downloads/yes/envs/tf_m1/lib/python3.8/site-packages/sklearn/model_selection/_validation.py:776: UserWarning: Scoring failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "/Users/vidhi/Downloads/yes/envs/tf_m1/lib/python3.8/site-packages/sklearn/model_selection/_validation.py", line 767, in _score
    scores = scorer(estimator, X_test, y_test)
  File "/Users/vidhi/Downloads/yes/envs/tf_m1/lib/python3.8/site-packages/sklearn/metrics/_scorer.py", line 219, in __call__
    return self._score(
  File "/Users/vidhi/Downloads/yes/envs/tf_m1/lib/python3.8/site-packages/sklearn/metrics/_scorer.py", line 267, in _score
    return self._sign * self._score_func(y_true, y_pred, **self._kwargs)
  File "/Users/vidhi/Downloads/yes/envs/tf_m1/lib/python3.8/site-packages/sklearn/metrics/_classification.py", line 211, in accuracy_score
    y_type, y_true, y_pred = _check_targets(y_true, y_pred)
  File "/U

/Users/vidhi/Downloads/yes/envs/tf_m1/lib/python3.8/site-packages/sklearn/model_selection/_validation.py:776: UserWarning: Scoring failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "/Users/vidhi/Downloads/yes/envs/tf_m1/lib/python3.8/site-packages/sklearn/model_selection/_validation.py", line 767, in _score
    scores = scorer(estimator, X_test, y_test)
  File "/Users/vidhi/Downloads/yes/envs/tf_m1/lib/python3.8/site-packages/sklearn/metrics/_scorer.py", line 219, in __call__
    return self._score(
  File "/Users/vidhi/Downloads/yes/envs/tf_m1/lib/python3.8/site-packages/sklearn/metrics/_scorer.py", line 267, in _score
    return self._sign * self._score_func(y_true, y_pred, **self._kwargs)
  File "/Users/vidhi/Downloads/yes/envs/tf_m1/lib/python3.8/site-packages/sklearn/metrics/_classification.py", line 211, in accuracy_score
    y_type, y_true, y_pred = _check_targets(y_true, y_pred)
  File "/U

/Users/vidhi/Downloads/yes/envs/tf_m1/lib/python3.8/site-packages/sklearn/model_selection/_validation.py:776: UserWarning: Scoring failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "/Users/vidhi/Downloads/yes/envs/tf_m1/lib/python3.8/site-packages/sklearn/model_selection/_validation.py", line 767, in _score
    scores = scorer(estimator, X_test, y_test)
  File "/Users/vidhi/Downloads/yes/envs/tf_m1/lib/python3.8/site-packages/sklearn/metrics/_scorer.py", line 219, in __call__
    return self._score(
  File "/Users/vidhi/Downloads/yes/envs/tf_m1/lib/python3.8/site-packages/sklearn/metrics/_scorer.py", line 267, in _score
    return self._sign * self._score_func(y_true, y_pred, **self._kwargs)
  File "/Users/vidhi/Downloads/yes/envs/tf_m1/lib/python3.8/site-packages/sklearn/metrics/_classification.py", line 211, in accuracy_score
    y_type, y_true, y_pred = _check_targets(y_true, y_pred)
  File "/U

...

/Users/vidhi/Downloads/yes/envs/tf_m1/lib/python3.8/site-packages/sklearn/model_selection/_validation.py:776: UserWarning: Scoring failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "/Users/vidhi/Downloads/yes/envs/tf_m1/lib/python3.8/site-packages/sklearn/model_selection/_validation.py", line 767, in _score
    scores = scorer(estimator, X_test, y_test)
  File "/Users/vidhi/Downloads/yes/envs/tf_m1/lib/python3.8/site-packages/sklearn/metrics/_scorer.py", line 219, in __call__
    return self._score(
  File "/Users/vidhi/Downloads/yes/envs/tf_m1/lib/python3.8/site-packages/sklearn/metrics/_scorer.py", line 267, in _score
    return self._sign * self._score_func(y_true, y_pred, **self._kwargs)
  File "/Users/vidhi/Downloads/yes/envs/tf_m1/lib/python3.8/site-packages/sklearn/metrics/_classification.py", line 211, in accuracy_score
    y_type, y_true, y_pred = _check_targets(y_true, y_pred)
  File "/U

/Users/vidhi/Downloads/yes/envs/tf_m1/lib/python3.8/site-packages/sklearn/model_selection/_validation.py:776: UserWarning: Scoring failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "/Users/vidhi/Downloads/yes/envs/tf_m1/lib/python3.8/site-packages/sklearn/model_selection/_validation.py", line 767, in _score
    scores = scorer(estimator, X_test, y_test)
  File "/Users/vidhi/Downloads/yes/envs/tf_m1/lib/python3.8/site-packages/sklearn/metrics/_scorer.py", line 219, in __call__
    return self._score(
  File "/Users/vidhi/Downloads/yes/envs/tf_m1/lib/python3.8/site-packages/sklearn/metrics/_scorer.py", line 267, in _score
    return self._sign * self._score_func(y_true, y_pred, **self._kwargs)
  File "/Users/vidhi/Downloads/yes/envs/tf_m1/lib/python3.8/site-packages/sklearn/metrics/_classification.py", line 211, in accuracy_score
    y_type, y_true, y_pred = _check_targets(y_true, y_pred)
  File "/U

/Users/vidhi/Downloads/yes/envs/tf_m1/lib/python3.8/site-packages/sklearn/model_selection/_validation.py:776: UserWarning: Scoring failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "/Users/vidhi/Downloads/yes/envs/tf_m1/lib/python3.8/site-packages/sklearn/model_selection/_validation.py", line 767, in _score
    scores = scorer(estimator, X_test, y_test)
  File "/Users/vidhi/Downloads/yes/envs/tf_m1/lib/python3.8/site-packages/sklearn/metrics/_scorer.py", line 219, in __call__
    return self._score(
  File "/Users/vidhi/Downloads/yes/envs/tf_m1/lib/python3.8/site-packages/sklearn/metrics/_scorer.py", line 267, in _score
    return self._sign * self._score_func(y_true, y_pred, **self._kwargs)
  File "/Users/vidhi/Downloads/yes/envs/tf_m1/lib/python3.8/site-packages/sklearn/metrics/_classification.py", line 211, in accuracy_score
    y_type, y_true, y_pred = _check_targets(y_true, y_pred)
  File "/U

/Users/vidhi/Downloads/yes/envs/tf_m1/lib/python3.8/site-packages/sklearn/model_selection/_validation.py:776: UserWarning: Scoring failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "/Users/vidhi/Downloads/yes/envs/tf_m1/lib/python3.8/site-packages/sklearn/model_selection/_validation.py", line 767, in _score
    scores = scorer(estimator, X_test, y_test)
  File "/Users/vidhi/Downloads/yes/envs/tf_m1/lib/python3.8/site-packages/sklearn/metrics/_scorer.py", line 219, in __call__
    return self._score(
  File "/Users/vidhi/Downloads/yes/envs/tf_m1/lib/python3.8/site-packages/sklearn/metrics/_scorer.py", line 267, in _score
    return self._sign * self._score_func(y_true, y_pred, **self._kwargs)
  File "/Users/vidhi/Downloads/yes/envs/tf_m1/lib/python3.8/site-packages/sklearn/metrics/_classification.py", line 211, in accuracy_score
    y_type, y_true, y_pred = _check_targets(y_true, y_pred)
  File "/U

KeyboardInterrupt: 

In [46]:
print(gs_svr.cv_results_) 

{'mean_fit_time': array([2.56997652, 2.49293716, 2.58732369, 2.66674883, 2.81026499,
       2.84159367, 2.88821604, 2.94105024, 3.57719636, 3.64354002,
       3.35307097, 3.35856419]), 'std_fit_time': array([0.07506518, 0.045572  , 0.0490366 , 0.0336026 , 0.04207001,
       0.03520413, 0.0403197 , 0.04404644, 0.08501487, 0.09685048,
       0.08082197, 0.06251381]), 'mean_score_time': array([0.38949304, 0.38887057, 0.40373778, 0.42161148, 0.43721237,
       0.43966856, 0.45498891, 0.46737351, 0.51372631, 0.56604419,
       0.50111842, 0.4740526 ]), 'std_score_time': array([0.01590395, 0.00895867, 0.01083688, 0.0061511 , 0.01254733,
       0.00917649, 0.01313321, 0.02769037, 0.02869045, 0.07220808,
       0.01286079, 0.06954149]), 'param_reg__estimator__C': masked_array(data=[0.01, 0.01, 0.01, 0.01, 0.1, 0.1, 0.1, 0.1, 1, 1, 1, 1],
             mask=[False, False, False, False, False, False, False, False,
                   False, False, False, False],
       fill_value='?',
            

In [24]:
print(gs_svr.best_estimator_) 

Pipeline(steps=[('reg', MultiOutputRegressor(estimator=SVR(C=0.01, degree=2)))])


In [39]:
accuracy=gs_svr.best_score_
print(accuracy)

nan


In [40]:
example_batch = normed_test_data
example_result = gs_svr.predict(example_batch)
example_result

array([[0.09999585, 0.10001515, 0.09996191, ..., 0.09985209, 0.10002139,
        0.09999568],
       [0.09999585, 0.10001515, 0.09996191, ..., 0.09985209, 0.10002139,
        0.09999568],
       [0.09999585, 0.10001515, 0.09996191, ..., 0.09985209, 0.10002139,
        0.09999568],
       ...,
       [0.09999585, 0.10001515, 0.09996191, ..., 0.09985209, 0.10002139,
        0.09999568],
       [0.09999585, 0.10001515, 0.09996191, ..., 0.09985209, 0.10002139,
        0.09999568],
       [0.09999585, 0.10001515, 0.09996191, ..., 0.09985209, 0.10002139,
        0.09999568]])

In [43]:
# gs_svr.score(normed_test_data,test_labels)

In [44]:
# Evaluate the regressor
mse_one = mean_squared_error(test_labels.iloc[:,0], example_result[:,0])
mse_two = mean_squared_error(test_labels.iloc[:,1], example_result[:,1])
print(f'MSE for first regressor: {mse_one} - second regressor: {mse_two}')
mae_one = mean_absolute_error(test_labels.iloc[:,0], example_result[:,0])
mae_two = mean_absolute_error(test_labels.iloc[:,1], example_result[:,1])
print(f'MAE for first regressor: {mae_one} - second regressor: {mae_two}')

MSE for first regressor: 0.036246161564981914 - second regressor: 0.1202350756905211
MAE for first regressor: 0.12624284201179237 - second regressor: 0.21024719349808535


In [47]:
index = 0
correct = 0
incorrect = 0
total = 0
for i in example_result:
    temp = np.array(example_result[index])
    predicted = temp.argsort()[-5:]
    actual = np.argmax(test_labels.iloc[index])
    if actual in predicted:
        correct+=1
    else:
        incorrect+=1
    total+=1
    index+=1
print(correct/total)
# np.argmax(example_result[1])

0.46981627296587924
